# Pipelene to find the best model

### Author
**Anna Igolkina** [e-mail](mailto:igolkinaanna11@gmail.com)  
2017-2018

### Include sources

In [1]:
# Fix sumething for "Random.seed" - Juryter raise the warning without it
rm(.Random.seed)
set.seed(1)

func_graph = "graph.R"
func_models = "models.R"
func_pathways = "pathways.R"
source(func_graph)
source(func_models)
source(func_pathways)


Warning message in rm(.Random.seed):
“объект '.Random.seed' не найден”Installing DiagrammeR
'/Library/Frameworks/R.framework/Resources/bin/R' --no-site-file --no-environ  \
  --no-save --no-restore --quiet CMD INSTALL  \
  '/Users/anna/OneDrive/polytech/schiza/scripts/sem_config/r-diagrammer-0.8.2-r3.3.1_0/lib/R/library/DiagrammeR'  \
  --library='/Library/Frameworks/R.framework/Versions/3.3/Resources/library'  \
  --install-tests 

This is lavaan 0.5-23.1097
lavaan is BETA software! Please report any bugs.


### Read data
We provide one table with all 255 samples in rows and (genes + additional factors) in columns
Then we divide data into two tables - for SCZ and for control group

In [2]:
dExpr = read.table('dExpr.txt')
dCon = dExpr[dExpr[,'disease'] == 0,]
dSch = dExpr[dExpr[,'disease'] == 1,]

# Covariates, which are common for both groups (disease and control)
common_factors = c('Age', 'Sex', 'Pca1', 'Pca2', 'batch')

### Select a pathway to work with and render the initial graph with ambiguities in nodes

In this example we selected MAPK pathway

In [3]:

# Pathway to use
pathway_name = 'MAPK'
# pathway_name = 'FocalAdh'
# pathway_name = 'Neurotrophin'
# pathway_name = 'AKT'
# pathway_name = 'Serine'

pathway = get_pathway(pathway_name)

# choose the type of graph
flag = FALSE # inital graph

property_mx = get_graph_properties(pathway, flag)
pathway$genes_mx = property_mx$genes_mx
pathway$edges_mx = property_mx$edges_mx

graph = construct_graph(pathway, flag)

render_graph(graph)

HTML widgets cannot be represented in plain text (need html)

### Create all possible models, estimate them and chose the best one by cfi, rmsea and tli criteria

In [4]:
# Create all possible path models
path_mod = construct_path_mod(pathway, common_factors)
sprintf('Number of models is %i', length(path_mod$group))

# Select the best model
est = estimate_path_mod(path_mod$group, dExpr, common_factors)

# Estimate all models
mod_group <- get_best_mod(est, path_mod)

[1] "Number of models is 192"

### Create the graph with estimations on edges

In [5]:
# Fit the pbtained multigroup model
fit_groups = sem(mod_group, data = dExpr, meanstructure = TRUE , fixed.x = FALSE, group = 'disease')

# Add label properies (estimations) to edges
pathway_fit = construct_pathway_fit(pathway, fit_groups, common_factors)

# Calculate Information criteria for two separate models
pathway_fit = get_indexes(pathway_fit, mod_group, fit_groups, dCon, dSch, common_factors);

# Construct a new graph
graph_fit = construct_graph(pathway_fit, TRUE)

# Add nodes to display Information criteria
for (i in 1:length(pathway_fit$indexes))
  graph_fit = add_node(graph_fit, label = pathway_fit$indexes[i], node = i)
graph_fit = set_node_attr(graph_fit, nodes = c(1:4), node_attr = 'color', values = 'white')

# Render the graph
render_graph(graph_fit)

HTML widgets cannot be represented in plain text (need html)